# Conversion funnel

install retentioneering if running from google.colab or for the first time:

In [ ]:
!pip3 install retentioneering

## Basic example

Conversion funnel is the basic first step in almost all product analytics workflow. To learn how to plot basic funnels in Retentioneering framework let’s work through a basic example. To start we need to import retentioneering, load sample dataset and update config:

In [1]:
import retentioneering

# load sample user behavior data as a pandas dataframe: 
data = retentioneering.datasets.load_simple_shop()

# update config to pass columns names:
retentioneering.config.update({
    'user_col': 'user_id',
    'event_col':'event',
    'event_time_col':'timestamp',
})

Function rete.funnel() plot simple conversion funnel:

In [2]:
data.rete.funnel(targets = ['catalog', 'cart', 'payment_done'])

targets is required parameter for rete.funnel() function and is a list of event names you are interested to plot on the funnel. For each specified target event we calculate absolute number of user_id’s, who reach this event at least once. Also percentage numbes (relative to total number and relative to previous stage) are shown.

Order of stages on the funnel corresponds to the order in which events are passed in targets parameter.

## Targets grouping

Sometimes during funnel analysis several events can have similar importance and it doesn’t matter which particular event was reached. In this case, multiple events we would like to group as one stage can be passed as sub-list in targets parameter. Let’s plot a funnel where we group ‘product1’ and ‘product2’:

In [3]:
data.rete.funnel(targets = ['catalog', ['product1', 'product2'], 'cart', 'payment_done'])

You can now see new ‘product1 | product2’ stage on the funnel with 2010 unique users who reached any product page (product1 or product2).

## User grouping

Sometimes it is useful to compare funnels side-bi-side of several user groups. For example, to have a quck comparison of funnels of users from different channels, or from test and control groups in A/B test, or to compare multiple behavioral segments and etc.

This can be done by passing list of collections of user id’s via groups parameter. To illustrate this functionality let’s plot funnels for two groups: users who converted to ‘payment_done’ and users who did not. First, we need to obtain two collections of user_ids and then pass it to groups parameters for rete.funnel function:

In [4]:
g1 = set(data[data['event']=='payment_done']['user_id'])
g2 = set(data['user_id']) - g1

data.rete.funnel(targets = ['catalog', ['product1', 'product2'], 'cart', 'payment_done'],
                 groups = (g1, g2),
                 group_names = ('converted', 'not_converted'))

We can immediately see at the high level how two groups compare between each other at particular stages. As expected not converted users are majority, and we can see that most of non_converted users lost after visiting cart. Interestly, for converted users we can see that some users add product to cart directly from the catalog, without visiting product page (for converted users more unique users visited cart page than product page).

Let’s consider another example when we compare funnels between multiple users groups segmented according to their behavior (read more about behavioral clustering here).

First, let’s cluster users with respect to their behavior:

In [5]:
data.rete.get_clusters(method='kmeans',
                       n_clusters=8,
                       feature_type='tfidf',
                       ngram_range=(1,1));

With the clustering procedure above we grouped users together in a groups with similar behavior. The dictionary containing lists of user ids for each cluster was assigned to rete.cluster_mapping attribute. Now, let’s plot funnels which compares several obtained clusters:

In [6]:
clus1_ids = data.rete.cluster_mapping[1]
clus2_ids = data.rete.cluster_mapping[2]
clus3_ids = data.rete.cluster_mapping[3]
clus6_ids = data.rete.cluster_mapping[6]

data.rete.funnel(targets = ['catalog', ['product1', 'product2'], 'cart', 'payment_done'],
                 groups = (clus1_ids, clus2_ids, clus3_ids, clus6_ids),
                 group_names = ('cluster 1', 'cluster 2', 'cluster 3', 'cluster 6'))

After such funnel plot we can immediately have the intuition about obtained clusters. Cluster 1 - very low motivated traffic which doesn’t go deeper than catalog level, cluster 2 - users who reach product level, but have lower conversion to cart, cluster 3 - those are highly motivated users with most of the convertions, cluster 6 - users who reach cart level but mostly churned somewhere between cart and payment_done events

To understand deeper what are the common behavioral patterns for each graph we can plot graphs or step matrix.